In [1]:
# Required key bits : num_CRs * avg_hop_count * avg_key_size(sl ~ 2 : ~ 2^(11-sl)) ~ 1000*2*(512 - 9 - 1) ~ 10^6 secure bits. 
                    # For every secure bit, ~3 bits(sifting and spotting) are required. 
                    # Error Correction : Randomly pick from the reservoir.  

# 1. Linear code : this file gets called in the Links.bb84() method. Takes in the required security level. Runs until a secure key is established.
# 2. One-time : Run at the start to store the secure bits in the lots of 2^10, with hamming parity embedded. Bob will correct the flipped bits.
# 3. Parallel code : This code file runs throughtout the program, the CRs take out the key bits they require.

In [2]:
import seaborn as sns
import matplotlib.pyplot as plt
import numpy as np
import time
import os
from sys import getsizeof
from scipy.optimize import curve_fit

In [3]:
# For writing data
data_subdirectory = "Data"
if not os.path.exists(data_subdirectory):
    os.makedirs(data_subdirectory)

# Setting the precision for floating points :
np.set_printoptions(precision=4)

In [4]:
# Define the hyperbolic function
def hyperbolic_fit(x, a, b):
    return a / x + b

In [5]:
def Size(var):
    print(f" Sys size : {getsizeof(var)}", end = ", ".rjust(8 - len(f"{getsizeof(var)}")))
    
    try:
        print(f" np size : {var.nbytes}", end = " ")
    except:
        print(" np size : NA", end = " ")

In [6]:
def test(vars, labels):
    '''
    Size and Type : Prints the label of the variable and the corresponding size(with overhead) and the numpy size(if applicable). Also shows the 
    datatype of the variable. All in a justified manner.

    Data Examples : Prints the first 10 elements of the very first dimension of an array/list (e.g. in case of a 3-D array, will print the 
    array[0, 0, :10] element). If the array is only 1-D, will print the first 10 elements. If it's a single variable, the value will be printed.
    Next to each array example, '*' will be printed. The number of '*' printed corresponding to an array shows its dimensions.
    '''
    max_len = len(max(labels, key = len))

    print("\nSize and Type :\n")
    for item, label in zip(vars, labels):
        print(f"{label} {':'.rjust(max_len + 2 - len(label))} ", end = " ") 
        Size(item), print("    ", type(item), end = " "), print("")

    print("\n\nData Examples :\n ")
    for item, label in zip(vars, labels):
        print(f"{label} {':'.rjust(max_len + 2 - len(label))} ", end = " ") 
        
        try :
            try :
                print(item[0, :10], "**")
            except :
                print(item[:10], "*")
        
        except :
            print(item)    

In [7]:
qkey_sl = {1 : 300, 2 : 200, 3 : 100}

# SL = cr.sl

In [8]:
write = False
eve_presence = 'Random'    #'Random'
ch_noise = 1e-4     # 0.000 - 0.300, 0.050 V/s QBER (eve detection)
eve_threshold = 20e-2    # QBER_threshold = eve_threshold - ch_noise ( 0.25(+-0.01) - 0.02 (+-0.001) = 0.23 +- 0.011 )

precision = 5e-5 + 5e-3    
error_threshold = eve_threshold - ch_noise - precision
# step = int(1000/in_range)
# elements = num_iter*in_range
# in_len = np.array([1000 for _ in range(in_range)], dtype = 'uint16')

In [9]:
num_keys = 1000
key_size = 1000
indices = np.arange(num_keys)

time_taken = np.zeros(num_keys, dtype = 'float32')    # avg time taken by a key of a certain length
QBERs = np.zeros(num_keys, dtype = 'float16')
KEY_RESERVOIR = []
KEY_RESERVOIR_len = np.zeros(num_keys, dtype = 'uint16')

Eve_detected = np.zeros(num_keys, dtype='uint8')

## Test and Checks

In [10]:
init_vars = [num_keys, key_size, write, eve_presence, ch_noise, eve_threshold, Eve_detected, KEY_RESERVOIR_len, time_taken, QBERs, KEY_RESERVOIR]
init_labels = "num_keys, key_size, write, eve_presence, ch_noise, eve_threshold, Eve_detected, KEY_RESERVOIR_len, time_taken, QBERs, KEY_RESERVOIR".split(", ")
    
test(init_vars, init_labels)


Size and Type :

num_keys           :   Sys size : 28    ,  np size : NA      <class 'int'> 
key_size           :   Sys size : 28    ,  np size : NA      <class 'int'> 
write              :   Sys size : 28    ,  np size : NA      <class 'bool'> 
eve_presence       :   Sys size : 47    ,  np size : NA      <class 'str'> 
ch_noise           :   Sys size : 24    ,  np size : NA      <class 'float'> 
eve_threshold      :   Sys size : 24    ,  np size : NA      <class 'float'> 
Eve_detected       :   Sys size : 1112  ,  np size : 1000      <class 'numpy.ndarray'> 
KEY_RESERVOIR_len  :   Sys size : 2112  ,  np size : 2000      <class 'numpy.ndarray'> 
time_taken         :   Sys size : 4112  ,  np size : 4000      <class 'numpy.ndarray'> 
QBERs              :   Sys size : 2112  ,  np size : 2000      <class 'numpy.ndarray'> 
KEY_RESERVOIR      :   Sys size : 56    ,  np size : NA      <class 'list'> 


Data Examples :
 
num_keys           :  1000
key_size           :  1000
write             

## Protocol

In [11]:
START = time.time()
I = 0
while I < num_keys :
    print(f"I = {I + 1}", end = "  :  ")
    
    start = time.time()
    %run ./Qiskit_rebuilt_4.ipynb
    time_taken[I] = round(time.time() - start, 4)

    QBERs[I] = QBER
    KEY_RESERVOIR.append(key)
    KEY_RESERVOIR_len[I] = len(key)

    Eve_detected[I] = ((QBER >= error_threshold) and eve) + ((QBER < error_threshold) and not eve)    # Whether or not the DETECTION of Eve is CORRECT

    print(f"###################################### Iteration {I + 1} complete ######################################")
    I += 1

total_time = time.time() - START
print(total_time)

I = 1  :  Unprocessed_key_len = 1022, KEY_LENGTH = 501, DATA_LENGTH = 511, order = 9
 Alice uncorrected key size (= 1022) not an exponent of 2 : 110111111001001010011011101110001011010000010011011010110110100001100000011001111101011000100101100000000001010000001000101000111001001011100000110100111111001010100111101110001000111011001010110011110100001110000000011001100110101001000011101111001100011110100100111010100100111110011110101101100100000010011110101010101000100111000000111001011111100011100101110000000101100111000101111000011101111110000110011010011011100100001010110011010110001110110001100001100110010010011101110100101100010000000110000101110001111110001010001000111000100011101110011011011101110001001101100110110101011001010110101100100111101110000111000011100011111100001110111101111011010001110001010001100100111101110101000111111001001000010001011110111110110000101000101010100111110001001001111111001001110111100000010101100010011110101111100000100101001101010001101110001100100

*time_taken[ ]* and *total_time* differ in that *total_time* also accounts for the rejected iterations of key generation

In [12]:
print(total_time)
elapsed_time = f"{str(int(total_time//3600))}h  {str( int((total_time%3600)//60) )}m  {str(int(total_time%60))}s"
elapsed_time

10075.809960842133


'2h  47m  55s'

In [13]:
SKGR = len(KEY_RESERVOIR_len)/total_time
SKGR

0.09924760430043089

In [14]:
# Open the files to write data to
title = f"\nKEY RESERVOIR[Noise {ch_noise}][Eve {eve_presence}][Eve Threshold {eve_threshold}] "
simulation_parameters = f"\nNumber of keys : {num_keys},   Aimed length of keys : {key_len}  \nEve Presence : {eve_presence},   Channel Noise : {ch_noise},   Eve's threshold : {eve_threshold},   Precision of Error Measurement : {precision},   Error Threshold : {error_threshold} \nTime Taken : {elapsed_time}\n"

avg_time_taken = sum([time_taken[I] for I in range(num_keys)])/num_keys   
avg_out_len = sum([out_len[I] for I in range(num_keys)])/num_keys
avg_QBERs = sum([QBERs[I] for I in range(num_keys)])/num_keys

NameError: name 'key_len' is not defined

In [ ]:
incorrect = len(Eve_detected) - sum(Eve_detected)
detection = f"Eve's detection was incorrect : {incorrect}/{sum(Eve_detected)} times (= {incorrect/sum(Eve_detected)} ); for QBER Threshold : {error_threshold}"
print(detection)
# print(max(sum(Eve_detected))) 
print(f'EveDetection[Noise {ch_noise}]')

plt.figure(figsize=(12, 5))

plt.xlabel(f'Key Index')
plt.ylabel(f'Times correctly detected Eve(out of {num_iter} keys)')
xticks = indices[::100]
plt.xticks(xticks)
plt.yticks(np.arange(maxtime_taken)+1))

plt.minorticks_on()
plt.grid(True)
plt.tight_layout()

plt.scatter(indices, sum(Eve_detected))
sns.lineplot(indices, time_taken, linestyle = '--')

In [ ]:
vars = [num_iter, in_range, in_len, write, eve_presence, ch_noise, eve_threshold, Eve_detected, avg_out_len, avg_time_taken, avg_QBERs, SKGR, keys]  
labels = "num_iter, in_range, in_len, write, eve_presence, ch_noise, eve_threshold, Eve_detected, avg_out_len, avg_time_taken, avg_QBERs, SKGR, keys".split(", ")

test(vars, labels)

In [ ]:
False_detections = [(i, j) for (i, j) in zip(np.where(Eve_detected == 0)[0], np.where(Eve_detected == 0)[1])]
print(False_detections[:9], '...')

In [ ]:
fig, ax = plt.subplots(2, 2, figsize=(12, 8))
# For key length
coefficients_len = np.polyfit(indices, KEY_RESERVOIR_len, 1)
polynomial_len = np.poly1d(coefficients_len)
equation_len = f'y = {coefficients_len[0]:.2f}x + {coefficients_len[1]:.2f}'
ax[0, 0].text(0.05, 0.95, equation_len, transform=ax[0, 0].transAxes, fontsize=10, verticalalignment='top')
ax[0, 0].set_xlabel('Indices')
ax[0, 0].set_ylabel('Length of final key after Information Reconciliation')
ax[0, 0].set_title("Key length")
ax[0, 0].plot(indices, KEY_RESERVOIR_len)
ax[0, 0].plot(indices, polynomial_len(indices), linestyle='--')
ax[0, 0].minorticks_on()
ax[0, 0].grid(True)

# For QBER
coefficients_qber = np.polyfit(indices, QBERs, 1)
polynomial_qber = np.poly1d(coefficients_qber)
equation_qber = f'y = {coefficients_qber[0]:.2f}x + {coefficients_qber[1]:.2f}'
ax[0, 1].text(0.05, 0.95, equation_qber, transform=ax[0, 1].transAxes, fontsize=10, verticalalignment='top')
ax[0, 1].set_xlabel('Indices')
ax[0, 1].set_ylabel('Average QBER')
ax[0, 1].set_title("QBER")
ax[0, 1].plot(indices, QBERs)
ax[0, 1].plot(indices, polynomial_qber(indices), linestyle='--')
ax[0, 1].minorticks_on()
ax[0, 1].grid(True)

# For time taken for 1 cycle
coefficients_tt = np.polyfit(indices, time_taken, 1) #sns.lineplot(np.arange(num_keys), time_taken, linestyle = '--')
polynomial_tt = np.poly1d(coefficients_tt)
equation_tt = f'y = {coefficients_tt[0]:.2f}x + {coefficients_tt[1]:.2f}'
ax[1, 0].text(0.05, 0.95, equation_tt, transform=ax[1, 0].transAxes, fontsize=10, verticalalignment='top')
ax[1, 0].set_xlabel('Indices')
ax[1, 0].set_ylabel('Time taken for 1 cycle')
ax[1, 0].set_title("Time taken")
ax[1, 0].plot(indices, time_taken)
ax[1, 0].plot(indices, polynomial_tt(indices), linestyle='--')
ax[1, 0].minorticks_on()
ax[1, 0].grid(True)

# Fit the data to the hyperbolic function
popt, pcov = curve_fit(hyperbolic_fit, indices, SKGR)
a, b = popt
# Generate the polynomial using the fitted parameters
fitted_SKGR = hyperbolic_fit(indices, *popt)
equation_SKGR = f'y = {a:.2f}/x + {b:.2f}'
ax[1, 1].text(0.05, 0.95, equation_SKGR, transform=ax[1, 1].transAxes, fontsize=10, verticalalignment='top')
ax[1, 1].set_xlabel('Indices of initial key')
ax[1, 1].set_ylabel('Secure key generation rate')
ax[1, 1].set_title("Input key indices vs SKGR")
ax[1, 1].plot(indices, SKGR, 'o', label='Data')  # Plot the original data
ax[1, 1].plot(indices, fitted_SKGR, linestyle='--', label='Hyperbolic fit')  # Plot the hyperbolic fit
ax[1, 1].minorticks_on()
ax[1, 1].grid(True)


# Set the super title for the entire figure
plt.suptitle(title, weight='bold')

# Display the plots
plt.tight_layout(rect=[0, 0.03, 1, 0.95])
plt.show()

# Print the title
print(title)


In [ ]:
if write :
    filename = f"Data.txt"
    key_strings = f"Keys.txt"
    data_path = os.path.join(data_subdirectory, filename)
    key_path = os.path.join(data_subdirectory, key_strings)
    file = open(data_path, "a")
    file2 = open(key_path, "a")
    
    file.write(simulation_parameters)
    file2.write(simulation_parameters)

    
    file.write(f"\nInput Length = [{', '.join(map(str, in_len))}] \nAverage Time Taken = [{', '.join(map(str, avg_time_taken))}] \nAverage QBER = [{', '.join(map(str, avg_QBERs))}] \nAverage Output length = [{', '.join(map(str, avg_out_len))}]\n \nSKGR = [{', '.join(map(str, SKGR))}]")
    file.close()
    
    file2.write(detection)
    file2.write(f" False detection indices : {False_detections}")
    file2.write(f"\nKeys = [{', '.join(map(str, keys))}] \n\n Eve detection = [{', '.join(map(str, Eve_detected))}]")
    file2.close()

    write = False
    print("Files updated")

In [ ]:
plt.plot(in_len, avg_out_len/1000, label = "Output length/1000")
plt.plot(in_len, avg_QBERs, label = "QBERs")
plt.plot(in_len, avg_time_taken/100, label = "time_taken/100")
plt.plot(in_len, SKGR, label = 'SKGR')

plt.xlabel('in_len')
plt.ylabel('counts')
plt.title(f'All parameters in one for {title}')
plt.legend()

print(f'All_parameters[Noise {ch_noise}]')